In [1]:

from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.embeddings.openai import OpenAIEmbeddings
from langchain.vectorstores import Pinecone
from langchain.llms import OpenAI

c:\Users\pijus\OneDrive\Desktop\New folder (6)\.venv\lib\site-packages\pinecone\data\index.py:1: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm


In [2]:
from dotenv import load_dotenv
load_dotenv()

True

In [3]:
import os

In [4]:
from langchain_community.document_loaders import HuggingFaceDatasetLoader

In [5]:
dataset_name = "Pijush2023/Yale_Psychilogy"
page_content_column = 'Biography'


loader = HuggingFaceDatasetLoader(dataset_name, page_content_column)

In [6]:
data = loader.load()

c:\Users\pijus\OneDrive\Desktop\New folder (6)\.venv\lib\site-packages\datasets\load.py:2547: FutureWarning: 'use_auth_token' was deprecated in favor of 'token' in version 2.14.0 and will be removed in 3.0.0.
You can remove this warning by passing 'token=<use_auth_token>' instead.
  warnings.warn(


In [7]:
data[:130]

[Document(page_content='"No biography provided. Are you Sarah R. Violette, APRN? Update your profile"', metadata={'ID': 1, 'Name': 'Sarah R. Violette, APRN', 'URL': 'https://www.ynhhs.org/physicians/sarah-r-violette', 'Specialty': 'Psychiatry', 'Location': 'New Haven', 'Hospital': 'YALE'}),
 Document(page_content='"Peter Morgan, MD, PhD, is chair of psychiatry at Yale New Haven Health\\u2019s Bridgeport Hospital. Dr. Morgan says he grew up interested in both physics and medicine.  \\u201cI like to understand how the world works, which is why I fell in love with physics,\\u201d he says. \\u201cAs for psychiatry, people have always come to me to help fix things and I have enjoyed helping others.\\u201d  Dr. Morgan says the best part of his job is feeling like he can make a positive difference in patients\\u2019 lives. \\u201cMany of the patients we serve have run into issues of not having access to treatment, being rejected from treatment, or not being comfortable accepting treatment,\\u

In [8]:
len(data)

130

In [9]:
from langchain_text_splitters import CharacterTextSplitter
text_splitter = CharacterTextSplitter(chunk_size=300, chunk_overlap=50)
documents = text_splitter.split_documents(data)

In [10]:
documents

[Document(page_content='"No biography provided. Are you Sarah R. Violette, APRN? Update your profile"', metadata={'ID': 1, 'Name': 'Sarah R. Violette, APRN', 'URL': 'https://www.ynhhs.org/physicians/sarah-r-violette', 'Specialty': 'Psychiatry', 'Location': 'New Haven', 'Hospital': 'YALE'}),
 Document(page_content='"Peter Morgan, MD, PhD, is chair of psychiatry at Yale New Haven Health\\u2019s Bridgeport Hospital. Dr. Morgan says he grew up interested in both physics and medicine.  \\u201cI like to understand how the world works, which is why I fell in love with physics,\\u201d he says. \\u201cAs for psychiatry, people have always come to me to help fix things and I have enjoyed helping others.\\u201d  Dr. Morgan says the best part of his job is feeling like he can make a positive difference in patients\\u2019 lives. \\u201cMany of the patients we serve have run into issues of not having access to treatment, being rejected from treatment, or not being comfortable accepting treatment,\\u

In [11]:

embeddings=OpenAIEmbeddings(api_key=os.environ['OPENAI_API_KEY'])
embeddings

c:\Users\pijus\OneDrive\Desktop\New folder (6)\.venv\lib\site-packages\langchain_core\_api\deprecation.py:119: LangChainDeprecationWarning: The class `OpenAIEmbeddings` was deprecated in LangChain 0.0.9 and will be removed in 0.3.0. An updated version of the class exists in the langchain-openai package and should be used instead. To use it run `pip install -U langchain-openai` and import as `from langchain_openai import OpenAIEmbeddings`.
  warn_deprecated(


OpenAIEmbeddings(client=<openai.resources.embeddings.Embeddings object at 0x000002B621E5EF10>, async_client=<openai.resources.embeddings.AsyncEmbeddings object at 0x000002B653CA9E50>, model='text-embedding-ada-002', deployment='text-embedding-ada-002', openai_api_version='', openai_api_base=None, openai_api_type='', openai_proxy='', embedding_ctx_length=8191, openai_api_key='sk-proj-4D5cMRuABdgIycWJqXmZT3BlbkFJTUlQRcMOgMKtbRbM7VJ8', openai_organization=None, allowed_special=set(), disallowed_special='all', chunk_size=1000, max_retries=2, request_timeout=None, headers=None, tiktoken_enabled=True, tiktoken_model_name=None, show_progress_bar=False, model_kwargs={}, skip_empty=False, default_headers=None, default_query=None, retry_min_seconds=4, retry_max_seconds=20, http_client=None)

In [12]:
vectors=embeddings.embed_query("How are you?")
len(vectors)

1536

In [13]:
# pip install pinecone-client


In [14]:
from pinecone import Pinecone, ServerlessSpec
pc = Pinecone(api_key='8dd4190f-17c6-4d0d-8b7e-6d011bbd4a7b')


In [15]:
index_name = "medical"

if index_name not in pc.list_indexes().names():
  pc.create_index(
      name=index_name,
      dimension=1536,
      metric='cosine',
      spec=ServerlessSpec(
          cloud='aws',
          region='us-east-1'
      )
  )


In [16]:
from langchain_pinecone import PineconeVectorStore


In [17]:
vectorstore = PineconeVectorStore(index_name=index_name, embedding=embeddings)
vectorstore.add_documents(documents)

['c1d308c7-20bd-4766-953e-ce63e4a7bb1d',
 'a9af1ec5-61d8-478d-9627-8aa09fd02cb1',
 '2093b388-3179-475a-9ef9-850b2a940e30',
 'c8ecbb5c-5a83-40c2-b158-ad7030652658',
 '7311fb09-66f4-4329-9ce4-1f28041743f7',
 '65aebee8-2a20-4276-a648-8e2d555d875f',
 'c1fc47c9-7cf6-4cee-aec6-a8b06413afef',
 '2e35a342-10f2-478e-9a55-954245ba69fb',
 'aedcb07e-669e-43ac-b9c8-c2b42626c9ce',
 '6da30039-f9c5-4788-b388-755e51f75384',
 '40690ac3-27bf-4029-9679-6bc4bc37101c',
 '4975f679-1f12-434f-b77b-671655190d12',
 'f61cdfac-b1e4-4096-8b6e-c37261ea4e7f',
 '755aa2f4-1f78-41aa-80e9-35f416ebe506',
 'f0b429db-ea00-4d4b-be53-43a07c6523f7',
 '515d606b-e9a0-4597-89dd-c0995f1498ca',
 '4cd099c5-963a-40f9-82ff-2c7932159e9d',
 '382db2ab-16fa-4cc9-b46d-6f5276412011',
 'e291dd4a-5575-4b25-81fd-c763c54803b1',
 'a35bc489-e369-4037-87fa-248b2efe88b3',
 '79c800ed-d4a4-410a-b045-2097340c1f7d',
 'd0af6c90-3cb1-4185-96f1-cd1f4b054182',
 '1a137ca9-1744-45cf-ac40-2b67aa6d35d4',
 'bdc9bd96-1b8f-42fc-9a2d-06d4c18bcb24',
 '0b68135d-b2c3-

In [18]:
documents

[Document(page_content='"No biography provided. Are you Sarah R. Violette, APRN? Update your profile"', metadata={'ID': 1, 'Name': 'Sarah R. Violette, APRN', 'URL': 'https://www.ynhhs.org/physicians/sarah-r-violette', 'Specialty': 'Psychiatry', 'Location': 'New Haven', 'Hospital': 'YALE', 'text': '"No biography provided. Are you Sarah R. Violette, APRN? Update your profile"'}),
 Document(page_content='"Peter Morgan, MD, PhD, is chair of psychiatry at Yale New Haven Health\\u2019s Bridgeport Hospital. Dr. Morgan says he grew up interested in both physics and medicine.  \\u201cI like to understand how the world works, which is why I fell in love with physics,\\u201d he says. \\u201cAs for psychiatry, people have always come to me to help fix things and I have enjoyed helping others.\\u201d  Dr. Morgan says the best part of his job is feeling like he can make a positive difference in patients\\u2019 lives. \\u201cMany of the patients we serve have run into issues of not having access to t

In [19]:
query = "who is the best doctor for depression?"
vectorstore.similarity_search(query,k=1)

[Document(page_content='"Dr. Sanacora is a Professor of Psychiatry at Yale University and the Director of the Yale Depression Research Program. Dr. Sanacora\\u2019s work has focused largely on elucidating the pathophysiological mechanisms associated with mood and other neuropsychiatric disorders and using this information to inform the development of novel treatment strategies. His preclinical research laboratory explores the effects of stress and pharmaceutical agents on cellular biology, neurophysiology and behavior. His clinical laboratory employs novel imaging methodologies to investigate the pathophysiology of mood and other neuropsychiatric disorders. In addition, he has served as principal investigator on several large clinical trials investigating the efficacy and safety of newly developed therapeutic agents for the treatment of mood disorders. Dr. Sanacora received the Anna-Monkia Stiftung international award for the investigation of the biological substrate and functional dis

In [20]:
retriever = vectorstore.as_retriever(search_kwargs={'k':1})

In [21]:
docs = retriever.invoke("who is the best doctors for depression ?")

In [22]:
docs

[Document(page_content='"Dr. Sanacora is a Professor of Psychiatry at Yale University and the Director of the Yale Depression Research Program. Dr. Sanacora\\u2019s work has focused largely on elucidating the pathophysiological mechanisms associated with mood and other neuropsychiatric disorders and using this information to inform the development of novel treatment strategies. His preclinical research laboratory explores the effects of stress and pharmaceutical agents on cellular biology, neurophysiology and behavior. His clinical laboratory employs novel imaging methodologies to investigate the pathophysiology of mood and other neuropsychiatric disorders. In addition, he has served as principal investigator on several large clinical trials investigating the efficacy and safety of newly developed therapeutic agents for the treatment of mood disorders. Dr. Sanacora received the Anna-Monkia Stiftung international award for the investigation of the biological substrate and functional dis

In [23]:
# !pip install langchain --upgrade
# !pip install openai --upgrade

In [24]:
from langchain_openai import ChatOpenAI
from langchain_core.output_parsers import StrOutputParser
from langchain import hub
from langchain_core.runnables import RunnablePassthrough,RunnableParallel

In [25]:
prompt=hub.pull("rlm/rag-prompt")

In [26]:
prompt

ChatPromptTemplate(input_variables=['context', 'question'], metadata={'lc_hub_owner': 'rlm', 'lc_hub_repo': 'rag-prompt', 'lc_hub_commit_hash': '50442af133e61576e74536c6556cefe1fac147cad032f4377b60c436e6cdcb6e'}, messages=[HumanMessagePromptTemplate(prompt=PromptTemplate(input_variables=['context', 'question'], template="You are an assistant for question-answering tasks. Use the following pieces of retrieved context to answer the question. If you don't know the answer, just say that you don't know. Use three sentences maximum and keep the answer concise.\nQuestion: {question} \nContext: {context} \nAnswer:"))])

In [33]:
# Instantiate chat model
chat_model= ChatOpenAI(api_key="sk-proj-4D5cMRuABdgIycWJqXmZT3BlbkFJTUlQRcMOgMKtbRbM7VJ8", temperature=0.5, model='gpt-3.5-turbo-0125')

In [34]:
rag_chain=(
    {"context":retriever , "question" : RunnablePassthrough()}
    | prompt
    | chat_model
    | StrOutputParser()
)

In [35]:
query="depression"
rag_chain.invoke(query)

'Dr. Gerard Sanacora is a Professor of Psychiatry at Yale University and the Director of the Yale Depression Research Program. His work focuses on understanding the pathophysiological mechanisms associated with mood and other neuropsychiatric disorders to develop novel treatment strategies. He has received awards for his research on the biological substrate and functional disturbances of depression.'

In [36]:
def generate_answer(message, history):
    return rag_chain.invoke(message)

In [37]:
import gradio as gr

In [40]:

# Set up chat bot interface
answer_bot = gr.ChatInterface(
                            generate_answer,
                            chatbot=gr.Chatbot(height=300),
                            textbox=gr.Textbox(placeholder="Ask me a question about Doctor on Psychiatry", container=False, scale=7),
                            title="Psychiatry Doctor Chat-Bot",
                            description="This is a chat bot related to top School in United States about Psychiatry",
                            theme="soft",
                            examples=["depression", "Mental-Stress", "Bipolar Disorder", "Eating Disorders" , "etc....."],
                            cache_examples=False,
                            retry_btn=None,
                            undo_btn=None,
                            clear_btn=None,
                            submit_btn="Ask"
                        )

In [41]:

answer_bot.launch()

Running on local URL:  http://127.0.0.1:7861

To create a public link, set `share=True` in `launch()`.
